In [2]:
# 导入所需的库
from math import gcd,log
from random import randint
import numpy as np
from qiskit import *
qasm_sim = qiskit.Aer.get_backend('qasm_simulator')

In [3]:
# 定义周期函数
def period(a,N):
    # 量子设备上可用的最大比特数
    available_qubits = 32 
    r=-1   
    
    if N >= 2**available_qubits:
        print(str(N)+' 对于IBMQ来说太大了')
    # 设计电路qc
    qr = QuantumRegister(available_qubits)   
    cr = ClassicalRegister(available_qubits)
    qc = QuantumCircuit(qr,cr)
    x0 = randint(1, N-1) 
    x_binary = np.zeros(available_qubits, dtype=bool)
    
    for i in range(1, available_qubits + 1):
        bit_state = (N%(2**i)!=0)
        if bit_state:
            N -= 2**(i-1)
        x_binary[available_qubits-i] = bit_state    
    
    for i in range(0,available_qubits):
        if x_binary[available_qubits-i-1]:
            qc.x(qr[i])
    x = x0
    
    while np.logical_or(x != x0, r <= 0):
        r+=1
        qc.measure(qr, cr) 
        for i in range(0,3): 
            qc.x(qr[i])
        qc.cx(qr[2],qr[1])
        qc.cx(qr[1],qr[2])
        qc.cx(qr[2],qr[1])
        qc.cx(qr[1],qr[0])
        qc.cx(qr[0],qr[1])
        qc.cx(qr[1],qr[0])
        qc.cx(qr[3],qr[0])
        qc.cx(qr[0],qr[1])
        qc.cx(qr[1],qr[0])
        
        result = execute(qc,backend = qasm_sim, shots=1024).result()
        counts = result.get_counts()
        print(qc)
        results = [[],[]]
        for key,value in counts.items(): #结果应该是确定性的，但可能存在一些量子计算错误，因此我们采用最近期的输出。
            results[0].append(key)
            results[1].append(int(value))
        s = results[0][np.argmax(np.array(results[1]))]
    return r

In [4]:
# 定义Shor分解函数
def shor(N):
    N = int(N)
    while True:
        a=randint(0,N-1)
        g=gcd(a,N)
        if g!=1 or N==1:
            return g,N//g
        else:
            r=period(a,N) 
            if r % 2 != 0:
                continue
            elif pow(a,r//2,N)==-1:
                continue
            else:
                p=gcd(pow(a,r//2)+1,N)
                q=gcd(pow(a,r//2)-1,N)
                if p==N or q==N:
                    continue
                return p,q

In [7]:
N=int(input("输入数字:"))
assert N>0,"输入应为正整数"
print(shor(N))

输入数字:108181
       ┌───┐                                                                 »
 q4_0: ┤ X ├─────────────────────────────────────────────────────────────────»
       └───┘┌─┐┌───┐                                                         »
 q4_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
       ┌───┐└╥┘└───┘                                                         »
 q4_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
       └───┘ ║  ┌─┐                                                          »
 q4_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
       ┌───┐ ║  └╥┘                                                          »
 q4_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
       └───┘ ║   ║  ┌─┐                                                      »
 q4_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
             ║   ║  └╥┘┌─┐              

       ┌───┐                                                                 »
 q4_0: ┤ X ├─────────────────────────────────────────────────────────────────»
       └───┘┌─┐┌───┐                                                         »
 q4_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
       ┌───┐└╥┘└───┘                                                         »
 q4_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
       └───┘ ║  ┌─┐                                                          »
 q4_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
       ┌───┐ ║  └╥┘                                                          »
 q4_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
       └───┘ ║   ║  ┌─┐                                                      »
 q4_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
             ║   ║  └╥┘┌─┐                          

       ┌───┐                                                                 »
 q5_0: ┤ X ├─────────────────────────────────────────────────────────────────»
       └───┘┌─┐┌───┐                                                         »
 q5_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
       ┌───┐└╥┘└───┘                                                         »
 q5_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
       └───┘ ║  ┌─┐                                                          »
 q5_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
       ┌───┐ ║  └╥┘                                                          »
 q5_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
       └───┘ ║   ║  ┌─┐                                                      »
 q5_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
             ║   ║  └╥┘┌─┐                          

       ┌───┐                                                                 »
 q5_0: ┤ X ├─────────────────────────────────────────────────────────────────»
       └───┘┌─┐┌───┐                                                         »
 q5_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
       ┌───┐└╥┘└───┘                                                         »
 q5_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
       └───┘ ║  ┌─┐                                                          »
 q5_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
       ┌───┐ ║  └╥┘                                                          »
 q5_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
       └───┘ ║   ║  ┌─┐                                                      »
 q5_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
             ║   ║  └╥┘┌─┐                          

       ┌───┐                                                                 »
 q6_0: ┤ X ├─────────────────────────────────────────────────────────────────»
       └───┘┌─┐┌───┐                                                         »
 q6_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
       ┌───┐└╥┘└───┘                                                         »
 q6_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
       └───┘ ║  ┌─┐                                                          »
 q6_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
       ┌───┐ ║  └╥┘                                                          »
 q6_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
       └───┘ ║   ║  ┌─┐                                                      »
 q6_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
             ║   ║  └╥┘┌─┐                          

...

        ┌───┐                                                                 »
 q66_0: ┤ X ├─────────────────────────────────────────────────────────────────»
        └───┘┌─┐┌───┐                                                         »
 q66_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
        ┌───┐└╥┘└───┘                                                         »
 q66_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
        └───┘ ║  ┌─┐                                                          »
 q66_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
        ┌───┐ ║  └╥┘                                                          »
 q66_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
        └───┘ ║   ║  ┌─┐                                                      »
 q66_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
              ║   ║  └╥┘┌─┐             

        ┌───┐                                                                 »
 q67_0: ┤ X ├─────────────────────────────────────────────────────────────────»
        └───┘┌─┐┌───┐                                                         »
 q67_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
        ┌───┐└╥┘└───┘                                                         »
 q67_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
        └───┘ ║  ┌─┐                                                          »
 q67_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
        ┌───┐ ║  └╥┘                                                          »
 q67_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
        └───┘ ║   ║  ┌─┐                                                      »
 q67_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
              ║   ║  └╥┘┌─┐             

        ┌───┐                                                                 »
 q67_0: ┤ X ├─────────────────────────────────────────────────────────────────»
        └───┘┌─┐┌───┐                                                         »
 q67_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
        ┌───┐└╥┘└───┘                                                         »
 q67_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
        └───┘ ║  ┌─┐                                                          »
 q67_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
        ┌───┐ ║  └╥┘                                                          »
 q67_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
        └───┘ ║   ║  ┌─┐                                                      »
 q67_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
              ║   ║  └╥┘┌─┐             

        ┌───┐                                                                 »
 q68_0: ┤ X ├─────────────────────────────────────────────────────────────────»
        └───┘┌─┐┌───┐                                                         »
 q68_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
        ┌───┐└╥┘└───┘                                                         »
 q68_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
        └───┘ ║  ┌─┐                                                          »
 q68_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
        ┌───┐ ║  └╥┘                                                          »
 q68_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
        └───┘ ║   ║  ┌─┐                                                      »
 q68_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
              ║   ║  └╥┘┌─┐             

        ┌───┐                                                                 »
 q68_0: ┤ X ├─────────────────────────────────────────────────────────────────»
        └───┘┌─┐┌───┐                                                         »
 q68_1: ─────┤M├┤ X ├─────────────────────────────────────────────────────────»
        ┌───┐└╥┘└───┘                                                         »
 q68_2: ┤ X ├─╫───────────────────────────────────────────────────────────────»
        └───┘ ║  ┌─┐                                                          »
 q68_3: ──────╫──┤M├──────────────────────────────────────────────────────────»
        ┌───┐ ║  └╥┘                                                          »
 q68_4: ┤ X ├─╫───╫───────────────────────────────────────────────────────────»
        └───┘ ║   ║  ┌─┐                                                      »
 q68_5: ──────╫───╫──┤M├──────────────────────────────────────────────────────»
              ║   ║  └╥┘┌─┐             